# Neo4J GDS 

https://neo4j.com/docs/graph-data-science/current/algorithms/pathfinding/

## Path finding

Path finding algorithms find the path between two or more nodes or evaluate the availability and quality of paths. The Neo4j GDS library includes the following path finding algorithms, grouped by quality tier:

#### Production-quality

- Delta-Stepping Single-Source Shortest Path

- Dijkstra Source-Target Shortest Path

- Dijkstra Single-Source Shortest Path

- A* Shortest Path

- Yen’s Shortest Path

- Breadth First Search

- Depth First Search

- Random Walk

- Bellman-Ford Single-Source Shortest Path

- Minimum Weight Spanning Tree

#### Beta

- Minimum Directed Steiner Tree

#### Alpha

- Minimum Weight k-Spanning Tree

- All Pairs Shortest Path

- Longest Path for DAG

In [4]:
from langchain.graphs import Neo4jGraph

graph = Neo4jGraph(
    url="bolt://100.26.193.165:7687",
    username="neo4j",
    password="tie-rubbish-word"
)

r = graph.query("""MATCH (n:Airport {city:"Los Angeles"}) RETURN n""")
print(r)

[{'n': {'altitude': 127, 'descr': 'Los Angeles International Airport', 'longest': 12091, 'iata': 'LAX', 'city': 'Los Angeles', 'icao': 'KLAX', 'location': POINT(-118.4079971 33.94250107), 'id': '13', 'pagerank': 8.193558075446687, 'runways': 4}}]


### Delta-Stepping Single-Source Shortest Path


https://neo4j.com/docs/graph-data-science/current/algorithms/delta-single-source/

The Delta-Stepping Shortest Path algorithm computes all shortest paths between a source node and all reachable nodes in the graph. The algorithm supports weighted graphs with positive relationship weights. To compute the shortest path between a source and a single target node, Dijkstra Source-Target can be used.

In contrast to Dijkstra Single-Source, the Delta-Stepping algorithm is a distance correcting algorithm. This property allows it to traverse the graph in parallel. The algorithm is guaranteed to always find the shortest path between a source node and a target node. However, if multiple shortest paths exist between two nodes, the algorithm is not guaranteed to return the same path in each computation..

In [5]:
# create new  Relationship HAS_ROUTE_WEIGHT and new attribute it "weight"
# UNCOMMENT THIS CELL TO CREATE THE RELATIONSHIP HAS_ROUTE_WEIGHT if is not Created

# create a new property in Country with the count of Airports in that country
r = graph.query("""MATCH (m:Country)
OPTIONAL MATCH (p:Airport)-[r:IN_COUNTRY]->(m:Country)
with  m,p, count(r) as num_airports
set m.num_airports = num_airports
set p.country_airports = num_airports
return m""")
print(len(r))

# create a new property in Region with the count of Airports in that Region
r = graph.query("""MATCH (m:Region)
OPTIONAL MATCH (p:Airport)-[r:IN_REGION]->(m:Region)
with  m,p, count(r) as num_airports
set m.num_airports = num_airports
set p.region_airports = num_airports
return m""")
print(len(r))

# create attribute in Relationship HAS_ROUTE_WEIGHT
"""
MATCH (p:Airport)-[r:HAS_ROUTE]->(m:Airport)
with  r, p, m, p.region_airports as region_airports, p.country_airports as country_airports, p.runways as runways
merge (p)-[:HAS_ROUTE_WEIGHT {weight : (region_airports* runways)/country_airports }]->(m) 

return p limit 25
"""

3503
3503


'\nMATCH (p:Airport)-[r:HAS_ROUTE]->(m:Airport)\nwith  r, p, m, p.region_airports as region_airports, p.country_airports as country_airports, p.runways as runways\nmerge (p)-[:HAS_ROUTE_WEIGHT {weight : (region_airports* runways)/country_airports }]->(m) \n\nreturn p limit 25\n'

In [6]:
r = graph.query("""
MATCH (p:Airport)-[r:HAS_ROUTE]->(m:Airport)
with  r, p, m, p.region_airports as region_airports, p.country_airports as country_airports, p.runways as runways
merge (p)-[:HAS_ROUTE_WEIGHT {weight : (region_airports* runways)/country_airports }]->(m) 

return p limit 25
""")
print(len(r))

25


### Delta

The delta parameter defines a range which is used to group nodes with the same tentative distance to the start node. The ranges are also called buckets. In each iteration of the algorithm, the non-empty bucket with the smallest tentative distance is processed in parallel. The delta parameter is the main tuning knob for the algorithm and controls the workload that can be processed in parallel. Generally, for power-law graphs, where many nodes can be reached within a few hops, a small delta (e.g. 2) is recommended. For high-diameter graphs, e.g. transport networks, a high delta value (e.g. 10000) is recommended. Note, that the value might vary depending on the graph topology and the value range of relationship properties.

In [ ]:
# Call gds.graph.drop("Graph_Airports")

In [163]:
r = graph.query("""CALL gds.graph.project(
    'myGraph',
    'Airport', 
    'HAS_ROUTE',
   {
        relationshipProperties: 'distance'
    }
);""")
print(r)

[{'nodeProjection': {'Airport': {'label': 'Airport', 'properties': {}}}, 'relationshipProjection': {'HAS_ROUTE': {'aggregation': 'DEFAULT', 'orientation': 'NATURAL', 'indexInverse': False, 'properties': {'distance': {'aggregation': 'DEFAULT', 'property': 'distance', 'defaultValue': None}}, 'type': 'HAS_ROUTE'}}, 'graphName': 'myGraph', 'nodeCount': 3503, 'relationshipCount': 46389, 'projectMillis': 104}]


In [8]:
r[-1]

{'nodeProjection': {'Airport': {'label': 'Airport', 'properties': {}}},
 'relationshipProjection': {'HAS_ROUTE': {'aggregation': 'DEFAULT',
   'orientation': 'NATURAL',
   'indexInverse': False,
   'properties': {'distance': {'aggregation': 'DEFAULT',
     'property': 'distance',
     'defaultValue': None}},
   'type': 'HAS_ROUTE'}},
 'graphName': 'myGraph',
 'nodeCount': 3503,
 'relationshipCount': 46389,
 'projectMillis': 9433}

In [ ]:
# We now run the Louvain algorithm to create a division of the nodes into communities that we can then evalutate.

In [164]:
r = graph.query("""MATCH (source:Airport {iata: 'BOS'})
CALL gds.allShortestPaths.delta.write.estimate('myGraph', {
    sourceNode: source,
    relationshipWeightProperty: 'distance',
    writeRelationshipType: 'PATH'
})
YIELD nodeCount, relationshipCount, bytesMin, bytesMax, requiredMemory
RETURN nodeCount, relationshipCount, bytesMin, bytesMax, requiredMemory""")
print(r)

[{'nodeCount': 3503, 'relationshipCount': 46389, 'bytesMin': 91384, 'bytesMax': 539568, 'requiredMemory': '[89 KiB ... 526 KiB]'}]


In [165]:
# unweighted
r = graph.query("""MATCH (source:Airport {descr: 'Boston Logan'})
CALL gds.allShortestPaths.delta.stream('myGraph', {
    sourceNode: source,
    relationshipWeightProperty: 'distance',
    delta: 3.0
})
YIELD index, sourceNode, targetNode, totalCost, nodeIds, costs, path
RETURN
    index,
    gds.util.asNode(sourceNode).descr AS sourceNodeName,
    gds.util.asNode(targetNode).descr AS targetNodeName,
    totalCost,
    [nodeId IN nodeIds | gds.util.asNode(nodeId).descr] AS nodeNames,
    costs,
    nodes(path) as path
ORDER BY totalCost
""")


In [123]:
len(r)

3292

In [166]:
print(r[0])

{'index': 4, 'sourceNodeName': 'Boston Logan', 'targetNodeName': 'Boston Logan', 'totalCost': 0.0, 'nodeNames': ['Boston Logan'], 'costs': [0.0], 'path': [{'altitude': 19, 'longest': 10083, 'city': 'Boston', 'descr': 'Boston Logan', 'iata': 'BOS', 'icao': 'KBOS', 'location': POINT(-71.00520325 42.36429977), 'id': '5', 'pagerank': 5.587850199484761, 'runways': 6, 'region_airports': 1, 'country_airports': 1}]}


In [167]:
print(r[0]['nodeNames'], r[0]['totalCost'])

['Boston Logan'] 0.0


In [168]:
print(r[1]['nodeNames'], r[1]['totalCost'])

['Boston Logan', 'Provincetown Municipal Airport'] 45.0


In [169]:
print(r[2]['nodeNames'], r[2]['totalCost'])

['Boston Logan', 'Barnstable Municipal Boardman Polando Field'] 61.0


In [170]:
print(r[-1]['nodeNames'], r[-1]['totalCost'])

['Boston Logan', 'Shanghai - Pudong International Airport', 'Bali - Ngurah Rai International Airport', 'Perth International Airport', 'Christmas Island Airport', 'Cocos (Keeling) Islands Airport'] 13912.0


In [171]:
# unweighted
r = graph.query("""Call gds.graph.drop("myGraph")
""")

print(r[0])

{'graphName': 'myGraph', 'database': 'neo4j', 'databaseLocation': 'local', 'memoryUsage': '', 'sizeInBytes': -1, 'nodeCount': 3503, 'relationshipCount': 46389, 'configuration': {'relationshipProjection': {'HAS_ROUTE': {'aggregation': 'DEFAULT', 'orientation': 'NATURAL', 'indexInverse': False, 'properties': {'distance': {'aggregation': 'DEFAULT', 'property': 'distance', 'defaultValue': None}}, 'type': 'HAS_ROUTE'}}, 'readConcurrency': 4, 'relationshipProperties': {}, 'nodeProperties': {}, 'jobId': '35ba7138-5824-414a-a5b4-bd3b8717fc26', 'nodeProjection': {'Airport': {'label': 'Airport', 'properties': {}}}, 'logProgress': True, 'creationTime': neo4j.time.DateTime(2024, 4, 15, 21, 43, 53, 467323202, tzinfo=<UTC>), 'validateRelationships': False, 'sudo': False}, 'density': 0.0037814532146957986, 'creationTime': neo4j.time.DateTime(2024, 4, 15, 21, 43, 53, 467323202, tzinfo=<UTC>), 'modificationTime': neo4j.time.DateTime(2024, 4, 15, 21, 43, 53, 574396691, tzinfo=<UTC>), 'schema': {'graphPr

### Dijkstra Source-Target Shortest Path


https://neo4j.com/docs/graph-data-science/current/algorithms/dijkstra-source-target/


The Dijkstra Shortest Path algorithm computes the shortest path between nodes. The algorithm supports weighted graphs with positive relationship weights. The Dijkstra Source-Target algorithm computes the shortest path between a source and a target node. To compute all paths from a source node to all reachable nodes, Dijkstra Single-Source can be used.

The GDS implementation is based on the original description and uses a binary heap as priority queue. The implementation is also used for the A* and Yen’s algorithms. The algorithm implementation is executed using a single thread. Altering the concurrency configuration has no effect.

In [172]:
r = graph.query("""CALL gds.graph.project(
    'myGraph',
    'Airport', 
    'HAS_ROUTE',
   {
        relationshipProperties: 'distance'
    }
);""")
print(r)

[{'nodeProjection': {'Airport': {'label': 'Airport', 'properties': {}}}, 'relationshipProjection': {'HAS_ROUTE': {'aggregation': 'DEFAULT', 'orientation': 'NATURAL', 'indexInverse': False, 'properties': {'distance': {'aggregation': 'DEFAULT', 'property': 'distance', 'defaultValue': None}}, 'type': 'HAS_ROUTE'}}, 'graphName': 'myGraph', 'nodeCount': 3503, 'relationshipCount': 46389, 'projectMillis': 94}]


# Memory Estimation 
If the results of the algorithm are as expected, the next step can be to write them back to the Neo4j database

In [173]:
r = graph.query("""MATCH (source:Airport {descr: 'Boston Logan'}), (target:Airport {descr: 'Marshall Islands International Airport'})
CALL gds.shortestPath.dijkstra.write.estimate('myGraph', {
    sourceNode: source,
    targetNode: target,
    relationshipWeightProperty: 'distance',
    writeRelationshipType: 'PATH'
})
YIELD nodeCount, relationshipCount, bytesMin, bytesMax, requiredMemory
RETURN nodeCount, relationshipCount, bytesMin, bytesMax, requiredMemory
""")

print(r)

[{'nodeCount': 3503, 'relationshipCount': 46389, 'bytesMin': 141264, 'bytesMax': 141264, 'requiredMemory': '137 KiB'}]


# Stream the results
In the stream execution mode, the algorithm returns the similarity score for each relationship.

In [174]:
r = graph.query("""MATCH (source:Airport {descr: 'Boston Logan'}), (target:Airport {descr: 'Marshall Islands International Airport'})
CALL gds.shortestPath.dijkstra.stream('myGraph', {
    sourceNode: source,
    targetNode: target,
    relationshipWeightProperty: 'distance'
})
YIELD index, sourceNode, targetNode, totalCost, nodeIds, costs, path
RETURN
    index,
    gds.util.asNode(sourceNode).descr AS sourceNodeName,
    gds.util.asNode(targetNode).descr AS targetNodeName,
    totalCost,
    [nodeId IN nodeIds | gds.util.asNode(nodeId).descr] AS nodeNames,
    costs,
    nodes(path) as path
ORDER BY index
""")



In [176]:
print(r)

[{'index': 0, 'sourceNodeName': 'Boston Logan', 'targetNodeName': 'Marshall Islands International Airport', 'totalCost': 7361.0, 'nodeNames': ['Boston Logan', 'Honolulu International Airport', 'Marshall Islands International Airport'], 'costs': [0.0, 5083.0, 7361.0], 'path': [{'altitude': 19, 'longest': 10083, 'city': 'Boston', 'descr': 'Boston Logan', 'iata': 'BOS', 'icao': 'KBOS', 'location': POINT(-71.00520325 42.36429977), 'id': '5', 'pagerank': 5.587850199484761, 'runways': 6, 'region_airports': 1, 'country_airports': 1}, {'altitude': 13, 'longest': 12312, 'city': 'Honolulu', 'descr': 'Honolulu International Airport', 'iata': 'HNL', 'icao': 'PHNL', 'location': POINT(-157.921997070312 21.3187007904053), 'id': '37', 'pagerank': 2.5656798354848074, 'runways': 4, 'region_airports': 1, 'country_airports': 1}, {'altitude': 6, 'longest': 7897, 'city': 'Majuro Atoll', 'descr': 'Marshall Islands International Airport', 'iata': 'MAJ', 'icao': 'PKMJ', 'location': POINT(171.272003173828 7.064

In [175]:
print(r[0]['nodeNames'], r[0]['totalCost'])

['Boston Logan', 'Honolulu International Airport', 'Marshall Islands International Airport'] 7361.0


In [177]:
r = graph.query("""MATCH (source:Airport {descr: 'Lagos,Murtala Muhammed International Airport'}), (target:Airport {descr: 'Marshall Islands International Airport'})
CALL gds.shortestPath.dijkstra.stream('myGraph', {
    sourceNode: source,
    targetNode: target,
    relationshipWeightProperty: 'distance'
})
YIELD index, sourceNode, targetNode, totalCost, nodeIds, costs, path
RETURN
    index,
    gds.util.asNode(sourceNode).descr AS sourceNodeName,
    gds.util.asNode(targetNode).descr AS targetNodeName,
    totalCost,
    [nodeId IN nodeIds | gds.util.asNode(nodeId).descr] AS nodeNames,
    costs,
    nodes(path) as path
ORDER BY index
""")

print(r)

[{'index': 0, 'sourceNodeName': 'Lagos,Murtala Muhammed International Airport', 'targetNodeName': 'Marshall Islands International Airport', 'totalCost': 12460.0, 'nodeNames': ['Lagos,Murtala Muhammed International Airport', 'Addis Ababa Bole International Airport', 'Singapore, Changi International Airport', 'Port Moresby Jacksons International Airport', 'Honiara International Airport', 'Bonriki International Airport', 'Marshall Islands International Airport'], 'costs': [0.0, 2432.0, 6940.0, 10004.0, 10878.0, 12047.0, 12460.0], 'path': [{'altitude': 135, 'longest': 11153, 'city': 'Lagos', 'descr': 'Lagos,Murtala Muhammed International Airport', 'iata': 'LOS', 'icao': 'DNMM', 'location': POINT(3.32116007804871 6.57737016677856), 'id': '224', 'pagerank': 2.6550329679561164, 'runways': 1, 'region_airports': 1, 'country_airports': 1}, {'altitude': 7630, 'longest': 12467, 'city': 'Addis Ababa', 'descr': 'Addis Ababa Bole International Airport', 'iata': 'ADD', 'icao': 'HAAB', 'location': POIN

In [178]:
print(r[0]['nodeNames'], r[0]['totalCost'])

['Lagos,Murtala Muhammed International Airport', 'Addis Ababa Bole International Airport', 'Singapore, Changi International Airport', 'Port Moresby Jacksons International Airport', 'Honiara International Airport', 'Bonriki International Airport', 'Marshall Islands International Airport'] 12460.0


### Dijkstra Single-Source Shortest Path



https://neo4j.com/docs/graph-data-science/current/algorithms/dijkstra-single-source/


To compute all paths from a source node to all reachable nodes, Dijkstra Single-Source can be used.

The GDS implementation is based on the original description and uses a binary heap as priority queue. The implementation is also used for the A* and Yen’s algorithms. The algorithm implementation is executed using a single thread. Altering the concurrency configuration has no effect.

In [179]:
r = graph.query("""MATCH (source:Airport {descr: 'Marshall Islands International Airport'})
CALL gds.allShortestPaths.dijkstra.stream('myGraph', {
    sourceNode: source,
    relationshipWeightProperty: 'distance'
})
YIELD index, sourceNode, targetNode, totalCost, nodeIds, costs, path
RETURN
    index,
    gds.util.asNode(sourceNode).descr AS sourceNodeName,
    gds.util.asNode(targetNode).descr AS targetNodeName,
    totalCost,
    [nodeId IN nodeIds | gds.util.asNode(nodeId).descr] AS nodeNames,
    costs,
    nodes(path) as path
ORDER BY totalCost
""")
r

[{'index': 0,
  'sourceNodeName': 'Marshall Islands International Airport',
  'targetNodeName': 'Marshall Islands International Airport',
  'totalCost': 0.0,
  'nodeNames': ['Marshall Islands International Airport'],
  'costs': [0.0],
  'path': [{'altitude': 6,
    'longest': 7897,
    'city': 'Majuro Atoll',
    'descr': 'Marshall Islands International Airport',
    'iata': 'MAJ',
    'icao': 'PKMJ',
    'location': POINT(171.272003173828 7.06476020812988),
    'id': '643',
    'pagerank': 0.420773184580687,
    'runways': 1,
    'region_airports': 1,
    'country_airports': 1}]},
 {'index': 1,
  'sourceNodeName': 'Marshall Islands International Airport',
  'targetNodeName': 'Bucholz Army Air Field',
  'totalCost': 268.0,
  'nodeNames': ['Marshall Islands International Airport',
   'Bucholz Army Air Field'],
  'costs': [0.0, 268.0],
  'path': [{'altitude': 6,
    'longest': 7897,
    'city': 'Majuro Atoll',
    'descr': 'Marshall Islands International Airport',
    'iata': 'MAJ',
    

In [180]:
len(r)

3290

In [182]:
r[-1]['nodeNames'], r[-1]['totalCost']

(['Marshall Islands International Airport',
  'Bonriki International Airport',
  'Honiara International Airport',
  'Port Moresby Jacksons International Airport',
  'Singapore, Changi International Airport',
  'King Abdulaziz International Airport',
  'Halim Perdanakusuma International Airport'],
 15059.0)

In [184]:
r[1]['nodeNames'], r[1]['totalCost']

(['Marshall Islands International Airport', 'Bucholz Army Air Field'], 268.0)

 # Delete Projection

In [185]:
r = graph.query(""" Call gds.graph.drop("myGraph")
""")

print(r)

[{'graphName': 'myGraph', 'database': 'neo4j', 'databaseLocation': 'local', 'memoryUsage': '', 'sizeInBytes': -1, 'nodeCount': 3503, 'relationshipCount': 46389, 'configuration': {'relationshipProjection': {'HAS_ROUTE': {'aggregation': 'DEFAULT', 'orientation': 'NATURAL', 'indexInverse': False, 'properties': {'distance': {'aggregation': 'DEFAULT', 'property': 'distance', 'defaultValue': None}}, 'type': 'HAS_ROUTE'}}, 'readConcurrency': 4, 'relationshipProperties': {}, 'nodeProperties': {}, 'jobId': 'ddc6d4c3-5078-4dc9-a4c1-fe8409369ce4', 'nodeProjection': {'Airport': {'label': 'Airport', 'properties': {}}}, 'logProgress': True, 'creationTime': neo4j.time.DateTime(2024, 4, 15, 21, 49, 35, 74459462, tzinfo=<UTC>), 'validateRelationships': False, 'sudo': False}, 'density': 0.0037814532146957986, 'creationTime': neo4j.time.DateTime(2024, 4, 15, 21, 49, 35, 74459462, tzinfo=<UTC>), 'modificationTime': neo4j.time.DateTime(2024, 4, 15, 21, 49, 35, 170135445, tzinfo=<UTC>), 'schema': {'graphPro

# A* Shortest Path
https://neo4j.com/docs/graph-data-science/current/algorithms/astar//
The A* (pronounced "A-Star") Shortest Path algorithm computes the shortest path between two nodes. A* is an informed search algorithm as it uses a heuristic function to guide the graph traversal. The algorithm supports weighted graphs with positive relationship weights.

Unlike Dijkstra’s shortest path algorithm, the next node to search from is not solely picked on the already computed distance. Instead, the algorithm combines the already computed distance with the result of a heuristic function. That function takes a node as input and returns a value that corresponds to the cost to reach the target node from that node. In each iteration, the graph traversal is continued from the node with the lowest combined cos

In GDS, the heuristic function used to guide the search is the haversine formula. The formula computes the distance between two points on a sphere given their longitudes and latitudes. The distance is computed in nautical miles.

In order to guarantee finding the optimal solution, i.e., the shortest path between two points, the heuristic must be admissible. To be admissible, the function must not overestimate the distance to the target, i.e., the lowest possible cost of a path must always be greater or equal to the heuristic.

This leads to a requirement on the relationship weights of the input graph. Relationship weights must represent the distance between two nodes and ideally scaled to nautical miles. Kilometers or miles also work, but the heuristic works best for nautical miles.


https://en.wikipedia.org/wiki/Haversine_formula

The haversine formula determines the great-circle distance between two points on a sphere given their longitudes and latitudes. Important in navigation, it is a special case of a more general formula in spherical trigonometry, the law of haversines, that relates the sides and angles of spherical triangles.
t.uadratic.

In [187]:

r = graph.query("""CREATE (a:Station {name: 'Kings Cross',         latitude: 51.5308, longitude: -0.1238}),
       (b:Station {name: 'Euston',              latitude: 51.5282, longitude: -0.1337}),
       (c:Station {name: 'Camden Town',         latitude: 51.5392, longitude: -0.1426}),
       (d:Station {name: 'Mornington Crescent', latitude: 51.5342, longitude: -0.1387}),
       (e:Station {name: 'Kentish Town',        latitude: 51.5507, longitude: -0.1402}),
       (a)-[:CONNECTION {distance: 0.7}]->(b),
       (b)-[:CONNECTION {distance: 1.3}]->(c),
       (b)-[:CONNECTION {distance: 0.7}]->(d),
       (d)-[:CONNECTION {distance: 0.6}]->(c),
       (c)-[:CONNECTION {distance: 1.3}]->(e);""")
print(r)

[]


In [188]:
r = graph.query("""CALL gds.graph.project(
    'myGraph',
    'Station',
    'CONNECTION',
    {
        nodeProperties: ['latitude', 'longitude'],
        relationshipProperties: 'distance'
    }
)""")
print(r[:20])

[{'nodeProjection': {'Station': {'label': 'Station', 'properties': {'longitude': {'property': 'longitude', 'defaultValue': None}, 'latitude': {'property': 'latitude', 'defaultValue': None}}}}, 'relationshipProjection': {'CONNECTION': {'aggregation': 'DEFAULT', 'orientation': 'NATURAL', 'indexInverse': False, 'properties': {'distance': {'aggregation': 'DEFAULT', 'property': 'distance', 'defaultValue': None}}, 'type': 'CONNECTION'}}, 'graphName': 'myGraph', 'nodeCount': 15, 'relationshipCount': 15, 'projectMillis': 25}]


In [189]:
r = graph.query("""MATCH (source:Station {name: 'Kings Cross'}), (target:Station {name: 'Kentish Town'})
CALL gds.shortestPath.astar.write.estimate('myGraph', {
    sourceNode: source,
    targetNode: target,
    latitudeProperty: 'latitude',
    longitudeProperty: 'longitude',
    writeRelationshipType: 'PATH'
})
YIELD nodeCount, relationshipCount, bytesMin, bytesMax, requiredMemory
RETURN nodeCount, relationshipCount, bytesMin, bytesMax, requiredMemory
""")


In [190]:
r

[{'nodeCount': 15,
  'relationshipCount': 15,
  'bytesMin': 1896,
  'bytesMax': 1896,
  'requiredMemory': '1896 Bytes'},
 {'nodeCount': 15,
  'relationshipCount': 15,
  'bytesMin': 1896,
  'bytesMax': 1896,
  'requiredMemory': '1896 Bytes'},
 {'nodeCount': 15,
  'relationshipCount': 15,
  'bytesMin': 1896,
  'bytesMax': 1896,
  'requiredMemory': '1896 Bytes'},
 {'nodeCount': 15,
  'relationshipCount': 15,
  'bytesMin': 1896,
  'bytesMax': 1896,
  'requiredMemory': '1896 Bytes'},
 {'nodeCount': 15,
  'relationshipCount': 15,
  'bytesMin': 1896,
  'bytesMax': 1896,
  'requiredMemory': '1896 Bytes'},
 {'nodeCount': 15,
  'relationshipCount': 15,
  'bytesMin': 1896,
  'bytesMax': 1896,
  'requiredMemory': '1896 Bytes'},
 {'nodeCount': 15,
  'relationshipCount': 15,
  'bytesMin': 1896,
  'bytesMax': 1896,
  'requiredMemory': '1896 Bytes'},
 {'nodeCount': 15,
  'relationshipCount': 15,
  'bytesMin': 1896,
  'bytesMax': 1896,
  'requiredMemory': '1896 Bytes'},
 {'nodeCount': 15,
  'relationsh

In [191]:
r = graph.query("""MATCH (source:Station {name: 'Kings Cross'}), (target:Station {name: 'Kentish Town'})
CALL gds.shortestPath.astar.stream('myGraph', {
    sourceNode: source,
    targetNode: target,
    latitudeProperty: 'latitude',
    longitudeProperty: 'longitude',
    relationshipWeightProperty: 'distance'
})
YIELD index, sourceNode, targetNode, totalCost, nodeIds, costs, path
RETURN
    index,
    gds.util.asNode(sourceNode).name AS sourceNodeName,
    gds.util.asNode(targetNode).name AS targetNodeName,
    totalCost,
    [nodeId IN nodeIds | gds.util.asNode(nodeId).name] AS nodeNames,
    costs,
    nodes(path) as path
ORDER BY index
""")
r

[{'index': 0,
  'sourceNodeName': 'Kings Cross',
  'targetNodeName': 'Kentish Town',
  'totalCost': 3.3,
  'nodeNames': ['Kings Cross', 'Euston', 'Camden Town', 'Kentish Town'],
  'costs': [0.0, 0.7, 2.0, 3.3],
  'path': [{'name': 'Kings Cross', 'latitude': 51.5308, 'longitude': -0.1238},
   {'name': 'Euston', 'latitude': 51.5282, 'longitude': -0.1337},
   {'name': 'Camden Town', 'latitude': 51.5392, 'longitude': -0.1426},
   {'name': 'Kentish Town', 'latitude': 51.5507, 'longitude': -0.1402}]},
 {'index': 0,
  'sourceNodeName': 'Kings Cross',
  'targetNodeName': 'Kentish Town',
  'totalCost': 3.3,
  'nodeNames': ['Kings Cross', 'Euston', 'Camden Town', 'Kentish Town'],
  'costs': [0.0, 0.7, 2.0, 3.3],
  'path': [{'name': 'Kings Cross', 'latitude': 51.5308, 'longitude': -0.1238},
   {'name': 'Euston', 'latitude': 51.5282, 'longitude': -0.1337},
   {'name': 'Camden Town', 'latitude': 51.5392, 'longitude': -0.1426},
   {'name': 'Kentish Town', 'latitude': 51.5507, 'longitude': -0.1402}]}

In [192]:
r = graph.query(""" Call gds.graph.drop("myGraph")
""")

print(r)

[{'graphName': 'myGraph', 'database': 'neo4j', 'databaseLocation': 'local', 'memoryUsage': '', 'sizeInBytes': -1, 'nodeCount': 15, 'relationshipCount': 15, 'configuration': {'relationshipProjection': {'CONNECTION': {'aggregation': 'DEFAULT', 'orientation': 'NATURAL', 'indexInverse': False, 'properties': {'distance': {'aggregation': 'DEFAULT', 'property': 'distance', 'defaultValue': None}}, 'type': 'CONNECTION'}}, 'readConcurrency': 4, 'relationshipProperties': {}, 'nodeProperties': {}, 'jobId': '79eb26ce-8b55-4825-bb59-cbac66086bc3', 'nodeProjection': {'Station': {'label': 'Station', 'properties': {'longitude': {'property': 'longitude', 'defaultValue': None}, 'latitude': {'property': 'latitude', 'defaultValue': None}}}}, 'logProgress': True, 'creationTime': neo4j.time.DateTime(2024, 4, 15, 22, 6, 4, 581917873, tzinfo=<UTC>), 'validateRelationships': False, 'sudo': False}, 'density': 0.07142857142857142, 'creationTime': neo4j.time.DateTime(2024, 4, 15, 22, 6, 4, 581917873, tzinfo=<UTC>)

# Yen’s Shortest Path algorithm
https://neo4j.com/docs/graph-data-science/current/algorithms/yens/

Yen’s Shortest Path algorithm computes a number of shortest paths between two nodes. The algorithm is often referred to as Yen’s k-Shortest Path algorithm, where k is the number of shortest paths to compute. The algorithm supports weighted graphs with positive relationship weights. It also respects parallel relationships between the same two nodes when computing multiple shortest paths.

For k = 1, the algorithm behaves exactly like Dijkstra’s shortest path algorithm and returns the shortest path. For k = 2, the algorithm returns the shortest path and the second shortest path between the same source and target node. Generally, for k = n, the algorithm computes at most n paths which are discovered in the order of their total cost.e of node.

In [193]:
r = graph.query("""CALL gds.graph.project(
    'myGraph',
    'Airport', 
    'HAS_ROUTE',
   {
        relationshipProperties: 'distance'
    }
);""")
print(r)

[{'nodeProjection': {'Airport': {'label': 'Airport', 'properties': {}}}, 'relationshipProjection': {'HAS_ROUTE': {'aggregation': 'DEFAULT', 'orientation': 'NATURAL', 'indexInverse': False, 'properties': {'distance': {'aggregation': 'DEFAULT', 'property': 'distance', 'defaultValue': None}}, 'type': 'HAS_ROUTE'}}, 'graphName': 'myGraph', 'nodeCount': 3503, 'relationshipCount': 46389, 'projectMillis': 32}]


In [194]:
r = graph.query("""MATCH (source:Airport {descr: 'Boston Logan'}), (target:Airport {descr: 'Marshall Islands International Airport'})
CALL gds.shortestPath.yens.write.estimate('myGraph', {
    sourceNode: source,
    targetNode: target,
    k:3,
    relationshipWeightProperty: 'distance',
    writeRelationshipType: 'PATH'
})
YIELD nodeCount, relationshipCount, bytesMin, bytesMax, requiredMemory
RETURN nodeCount, relationshipCount, bytesMin, bytesMax, requiredMemory
""")

print(r)

[{'nodeCount': 3503, 'relationshipCount': 46389, 'bytesMin': 791096, 'bytesMax': 791096, 'requiredMemory': '772 KiB'}]


In [195]:
r = graph.query("""MATCH (source:Airport {descr: 'Lagos,Murtala Muhammed International Airport'}), (target:Airport {descr: 'Marshall Islands International Airport'})
CALL gds.shortestPath.yens.stream('myGraph', {
    sourceNode: source,
    targetNode: target,
     k: 3,
    relationshipWeightProperty: 'distance'
})
YIELD index, sourceNode, targetNode, totalCost, nodeIds, costs, path
RETURN
    index,
    gds.util.asNode(sourceNode).descr AS sourceNodeName,
    gds.util.asNode(targetNode).descr AS targetNodeName,
    totalCost,
    [nodeId IN nodeIds | gds.util.asNode(nodeId).descr] AS nodeNames,
    costs,
    nodes(path) as path
ORDER BY index
""")

print(r)

[{'index': 0, 'sourceNodeName': 'Lagos,Murtala Muhammed International Airport', 'targetNodeName': 'Marshall Islands International Airport', 'totalCost': 12460.0, 'nodeNames': ['Lagos,Murtala Muhammed International Airport', 'Addis Ababa Bole International Airport', 'Singapore, Changi International Airport', 'Port Moresby Jacksons International Airport', 'Honiara International Airport', 'Bonriki International Airport', 'Marshall Islands International Airport'], 'costs': [0.0, 2432.0, 6940.0, 10004.0, 10878.0, 12047.0, 12460.0], 'path': [{'altitude': 135, 'longest': 11153, 'city': 'Lagos', 'descr': 'Lagos,Murtala Muhammed International Airport', 'iata': 'LOS', 'icao': 'DNMM', 'location': POINT(3.32116007804871 6.57737016677856), 'id': '224', 'pagerank': 2.6550329679561164, 'runways': 1, 'region_airports': 1, 'country_airports': 1}, {'altitude': 7630, 'longest': 12467, 'city': 'Addis Ababa', 'descr': 'Addis Ababa Bole International Airport', 'iata': 'ADD', 'icao': 'HAAB', 'location': POIN

In [196]:
len(r)

3

In [197]:
r[0]['nodeNames'],r[0]['totalCost']

(['Lagos,Murtala Muhammed International Airport',
  'Addis Ababa Bole International Airport',
  'Singapore, Changi International Airport',
  'Port Moresby Jacksons International Airport',
  'Honiara International Airport',
  'Bonriki International Airport',
  'Marshall Islands International Airport'],
 12460.0)

In [198]:
r[1]['nodeNames'],r[1]['totalCost']

(['Lagos,Murtala Muhammed International Airport',
  'Akanu Ibiam International Airport',
  'Addis Ababa Bole International Airport',
  'Singapore, Changi International Airport',
  'Port Moresby Jacksons International Airport',
  'Honiara International Airport',
  'Bonriki International Airport',
  'Marshall Islands International Airport'],
 12463.0)

In [199]:
r[2]['nodeNames'],r[2]['totalCost']

(['Lagos,Murtala Muhammed International Airport',
  'New York John F. Kennedy International Airport',
  'Honolulu International Airport',
  'Marshall Islands International Airport'],
 12493.0)

In [200]:
r = graph.query("""Call gds.graph.drop("myGraph")""")
print(r)

[{'graphName': 'myGraph', 'database': 'neo4j', 'databaseLocation': 'local', 'memoryUsage': '', 'sizeInBytes': -1, 'nodeCount': 3503, 'relationshipCount': 46389, 'configuration': {'relationshipProjection': {'HAS_ROUTE': {'aggregation': 'DEFAULT', 'orientation': 'NATURAL', 'indexInverse': False, 'properties': {'distance': {'aggregation': 'DEFAULT', 'property': 'distance', 'defaultValue': None}}, 'type': 'HAS_ROUTE'}}, 'readConcurrency': 4, 'relationshipProperties': {}, 'nodeProperties': {}, 'jobId': '395bef51-5dc8-4e69-8361-1eacfd7bddd6', 'nodeProjection': {'Airport': {'label': 'Airport', 'properties': {}}}, 'logProgress': True, 'creationTime': neo4j.time.DateTime(2024, 4, 15, 22, 8, 22, 737862127, tzinfo=<UTC>), 'validateRelationships': False, 'sudo': False}, 'density': 0.0037814532146957986, 'creationTime': neo4j.time.DateTime(2024, 4, 15, 22, 8, 22, 737862127, tzinfo=<UTC>), 'modificationTime': neo4j.time.DateTime(2024, 4, 15, 22, 8, 22, 771539214, tzinfo=<UTC>), 'schema': {'graphProp

# Breadth First Search

https://neo4j.com/docs/graph-data-science/current/algorithms/bfs/

The Breadth First Search algorithm is a graph traversal algorithm that given a start node visits nodes in order of increasing distance, see 
https://en.wikipedia.org/wiki/Breadth-first_search

A related algorithm is the Depth First Search algorithm, Depth First Search. This algorithm is useful for searching when the likelihood of finding the node searched for decreases with distance. There are multiple termination conditions supported for the traversal, based on either reaching one of several target nodes, reaching a maximum depth, exhausting a given budget of traversed relationship cost, or just traversing the whole graph. The output of the procedure contains information about which nodes were visited and in what order..

DPS https://en.wikipedia.org/wiki/Depth-first_search


In [201]:
#Create Graph projection
r = graph.query("""CALL gds.graph.project('myGraph', 'Airport', 'HAS_ROUTE')""")
print(r)

[{'nodeProjection': {'Airport': {'label': 'Airport', 'properties': {}}}, 'relationshipProjection': {'HAS_ROUTE': {'aggregation': 'DEFAULT', 'orientation': 'NATURAL', 'indexInverse': False, 'properties': {}, 'type': 'HAS_ROUTE'}}, 'graphName': 'myGraph', 'nodeCount': 3503, 'relationshipCount': 46389, 'projectMillis': 32}]


In [202]:
#Overlap similarity function
r = graph.query("""MATCH (source:Airport {descr: 'Marshall Islands International Airport'})
CALL gds.bfs.stream.estimate('myGraph', {
    sourceNode: source
})
YIELD nodeCount, relationshipCount, bytesMin, bytesMax, requiredMemory
RETURN nodeCount, relationshipCount, bytesMin, bytesMax, requiredMemory""")
print(r)

[{'nodeCount': 3503, 'relationshipCount': 46389, 'bytesMin': 141510, 'bytesMax': 225550, 'requiredMemory': '[138 KiB ... 220 KiB]'}]


In [203]:
#Cosine similarity function
r = graph.query("""MATCH (source:Airport{descr:'Marshall Islands International Airport'}), (d:Airport{descr:'Boston Logan'}), (e:Airport{descr:'Abu Dhabi International Airport'})
WITH source, [d, e] AS targetNodes
CALL gds.bfs.stream('myGraph', {
  sourceNode: source,
  targetNodes: targetNodes
})
YIELD path
RETURN path""")
print(r)

[{'path': [{'altitude': 6, 'longest': 7897, 'city': 'Majuro Atoll', 'descr': 'Marshall Islands International Airport', 'iata': 'MAJ', 'icao': 'PKMJ', 'location': POINT(171.272003173828 7.06476020812988), 'id': '643', 'pagerank': 0.420773184580687, 'runways': 1, 'region_airports': 1, 'country_airports': 1}, 'NEXT', {'altitude': 13, 'longest': 12312, 'city': 'Honolulu', 'descr': 'Honolulu International Airport', 'iata': 'HNL', 'icao': 'PHNL', 'location': POINT(-157.921997070312 21.3187007904053), 'id': '37', 'pagerank': 2.5656798354848074, 'runways': 4, 'region_airports': 1, 'country_airports': 1}, 'NEXT', {'altitude': 9, 'longest': 6598, 'city': 'Tarawa', 'descr': 'Bonriki International Airport', 'iata': 'TRW', 'icao': 'NGTA', 'location': POINT(173.147003173828 1.38163995742798), 'id': '645', 'pagerank': 0.8259804469680505, 'runways': 1, 'region_airports': 1, 'country_airports': 1}, 'NEXT', {'altitude': 22, 'longest': 7054, 'city': 'Yaren District', 'descr': 'Nauru International Airport

In [204]:
len(r[0]['path'])

17

In [205]:
for d in r[0]['path']:
    print(d)

{'altitude': 6, 'longest': 7897, 'city': 'Majuro Atoll', 'descr': 'Marshall Islands International Airport', 'iata': 'MAJ', 'icao': 'PKMJ', 'location': POINT(171.272003173828 7.06476020812988), 'id': '643', 'pagerank': 0.420773184580687, 'runways': 1, 'region_airports': 1, 'country_airports': 1}
NEXT
{'altitude': 13, 'longest': 12312, 'city': 'Honolulu', 'descr': 'Honolulu International Airport', 'iata': 'HNL', 'icao': 'PHNL', 'location': POINT(-157.921997070312 21.3187007904053), 'id': '37', 'pagerank': 2.5656798354848074, 'runways': 4, 'region_airports': 1, 'country_airports': 1}
NEXT
{'altitude': 9, 'longest': 6598, 'city': 'Tarawa', 'descr': 'Bonriki International Airport', 'iata': 'TRW', 'icao': 'NGTA', 'location': POINT(173.147003173828 1.38163995742798), 'id': '645', 'pagerank': 0.8259804469680505, 'runways': 1, 'region_airports': 1, 'country_airports': 1}
NEXT
{'altitude': 22, 'longest': 7054, 'city': 'Yaren District', 'descr': 'Nauru International Airport', 'iata': 'INU', 'icao

In [206]:
#Cosine similarity function
r = graph.query("""MATCH (source:Airport{descr:'Marshall Islands International Airport'}), (d:Airport{descr:'Boston Logan'}), (e:Airport{descr:'Abu Dhabi International Airport'})
WITH source, [d, e] AS targetNodes
CALL gds.bfs.stream('myGraph', {
  sourceNode: source,
  targetNodes: targetNodes,  
  maxDepth: 1
})
YIELD path
RETURN path""")
print(r)

[{'path': [{'altitude': 6, 'longest': 7897, 'city': 'Majuro Atoll', 'descr': 'Marshall Islands International Airport', 'iata': 'MAJ', 'icao': 'PKMJ', 'location': POINT(171.272003173828 7.06476020812988), 'id': '643', 'pagerank': 0.420773184580687, 'runways': 1, 'region_airports': 1, 'country_airports': 1}, 'NEXT', {'altitude': 13, 'longest': 12312, 'city': 'Honolulu', 'descr': 'Honolulu International Airport', 'iata': 'HNL', 'icao': 'PHNL', 'location': POINT(-157.921997070312 21.3187007904053), 'id': '37', 'pagerank': 2.5656798354848074, 'runways': 4, 'region_airports': 1, 'country_airports': 1}, 'NEXT', {'altitude': 9, 'longest': 6598, 'city': 'Tarawa', 'descr': 'Bonriki International Airport', 'iata': 'TRW', 'icao': 'NGTA', 'location': POINT(173.147003173828 1.38163995742798), 'id': '645', 'pagerank': 0.8259804469680505, 'runways': 1, 'region_airports': 1, 'country_airports': 1}, 'NEXT', {'altitude': 22, 'longest': 7054, 'city': 'Yaren District', 'descr': 'Nauru International Airport

In [207]:
for d in r[0]['path']:
    print(d)

{'altitude': 6, 'longest': 7897, 'city': 'Majuro Atoll', 'descr': 'Marshall Islands International Airport', 'iata': 'MAJ', 'icao': 'PKMJ', 'location': POINT(171.272003173828 7.06476020812988), 'id': '643', 'pagerank': 0.420773184580687, 'runways': 1, 'region_airports': 1, 'country_airports': 1}
NEXT
{'altitude': 13, 'longest': 12312, 'city': 'Honolulu', 'descr': 'Honolulu International Airport', 'iata': 'HNL', 'icao': 'PHNL', 'location': POINT(-157.921997070312 21.3187007904053), 'id': '37', 'pagerank': 2.5656798354848074, 'runways': 4, 'region_airports': 1, 'country_airports': 1}
NEXT
{'altitude': 9, 'longest': 6598, 'city': 'Tarawa', 'descr': 'Bonriki International Airport', 'iata': 'TRW', 'icao': 'NGTA', 'location': POINT(173.147003173828 1.38163995742798), 'id': '645', 'pagerank': 0.8259804469680505, 'runways': 1, 'region_airports': 1, 'country_airports': 1}
NEXT
{'altitude': 22, 'longest': 7054, 'city': 'Yaren District', 'descr': 'Nauru International Airport', 'iata': 'INU', 'icao

In [208]:
#Cosine similarity function
r = graph.query("""MATCH (source:Airport{descr:'Marshall Islands International Airport'}), (d:Airport{descr:'Boston Logan'}), (e:Airport{descr:'Abu Dhabi International Airport'})
WITH source, [d, e] AS targetNodes
CALL gds.bfs.stream('myGraph', {
  sourceNode: source,
  targetNodes: targetNodes,  
  maxDepth: 3
})
YIELD path
RETURN path""")


In [209]:
for d in r[0]['path']:
    print(d)

{'altitude': 6, 'longest': 7897, 'city': 'Majuro Atoll', 'descr': 'Marshall Islands International Airport', 'iata': 'MAJ', 'icao': 'PKMJ', 'location': POINT(171.272003173828 7.06476020812988), 'id': '643', 'pagerank': 0.420773184580687, 'runways': 1, 'region_airports': 1, 'country_airports': 1}
NEXT
{'altitude': 13, 'longest': 12312, 'city': 'Honolulu', 'descr': 'Honolulu International Airport', 'iata': 'HNL', 'icao': 'PHNL', 'location': POINT(-157.921997070312 21.3187007904053), 'id': '37', 'pagerank': 2.5656798354848074, 'runways': 4, 'region_airports': 1, 'country_airports': 1}
NEXT
{'altitude': 9, 'longest': 6598, 'city': 'Tarawa', 'descr': 'Bonriki International Airport', 'iata': 'TRW', 'icao': 'NGTA', 'location': POINT(173.147003173828 1.38163995742798), 'id': '645', 'pagerank': 0.8259804469680505, 'runways': 1, 'region_airports': 1, 'country_airports': 1}
NEXT
{'altitude': 22, 'longest': 7054, 'city': 'Yaren District', 'descr': 'Nauru International Airport', 'iata': 'INU', 'icao

# Depth First Search

https://neo4j.com/docs/graph-data-science/current/algorithms/dfs/

The Depth First Search algorithm is a graph traversal that starts at a given node and explores as far as possible along each branch before backtracking, see https://en.wikipedia.org/wiki/Depth-first_search
DPS https://en.wikipedia.org/wiki/Depth-first_search

In [210]:
#Cosine similarity function
r = graph.query("""MATCH (source:Airport{descr:'Marshall Islands International Airport'}), (d:Airport{descr:'Boston Logan'}), (e:Airport{descr:'Abu Dhabi International Airport'})
WITH source, [d, e] AS targetNodes
CALL gds.dfs.stream('myGraph', {
  sourceNode: source,
  targetNodes: targetNodes

})
YIELD path
RETURN path""")


In [211]:
len(r[0]['path'])

4333

In [63]:
for d in r[0]['path']:
    print(d)

{'altitude': 6, 'longest': 7897, 'city': 'Majuro Atoll', 'descr': 'Marshall Islands International Airport', 'iata': 'MAJ', 'icao': 'PKMJ', 'location': POINT(171.272003173828 7.06476020812988), 'id': '643', 'pagerank': 0.420773184580687, 'runways': 1, 'region_airports': 1, 'country_airports': 1}
NEXT
{'altitude': 9, 'longest': 6668, 'city': 'Kwajalein', 'descr': 'Bucholz Army Air Field', 'iata': 'KWA', 'icao': 'PKWA', 'location': POINT(167.731994628906 8.72012042999268), 'id': '2395', 'pagerank': 0.2392602156916488, 'runways': 1, 'region_airports': 1, 'country_airports': 1}
NEXT
{'altitude': 22, 'longest': 7054, 'city': 'Yaren District', 'descr': 'Nauru International Airport', 'iata': 'INU', 'icao': 'ANYN', 'location': POINT(166.919006 -0.547458), 'id': '646', 'pagerank': 0.407279849931849, 'runways': 1, 'region_airports': 1, 'country_airports': 1}
NEXT
{'altitude': 13, 'longest': 11680, 'city': 'Brisbane', 'descr': 'Brisbane International Airport', 'iata': 'BNE', 'icao': 'YBBN', 'locat

In [212]:
#Cosine similarity function
r = graph.query("""MATCH (source:Airport{descr:'Marshall Islands International Airport'}), (d:Airport{descr:'Boston Logan'}), (e:Airport{descr:'Abu Dhabi International Airport'})
WITH source, [d, e] AS targetNodes
CALL gds.dfs.stream('myGraph', {
  sourceNode: source,
  targetNodes: targetNodes, 
   maxDepth: 7

})
YIELD path
RETURN path""")

In [213]:
len(r[0]['path'])

4333

In [214]:
for d in r[0]['path']:
    print(d)

{'altitude': 6, 'longest': 7897, 'city': 'Majuro Atoll', 'descr': 'Marshall Islands International Airport', 'iata': 'MAJ', 'icao': 'PKMJ', 'location': POINT(171.272003173828 7.06476020812988), 'id': '643', 'pagerank': 0.420773184580687, 'runways': 1, 'region_airports': 1, 'country_airports': 1}
NEXT
{'altitude': 9, 'longest': 6668, 'city': 'Kwajalein', 'descr': 'Bucholz Army Air Field', 'iata': 'KWA', 'icao': 'PKWA', 'location': POINT(167.731994628906 8.72012042999268), 'id': '2395', 'pagerank': 0.2392602156916488, 'runways': 1, 'region_airports': 1, 'country_airports': 1}
NEXT
{'altitude': 22, 'longest': 7054, 'city': 'Yaren District', 'descr': 'Nauru International Airport', 'iata': 'INU', 'icao': 'ANYN', 'location': POINT(166.919006 -0.547458), 'id': '646', 'pagerank': 0.407279849931849, 'runways': 1, 'region_airports': 1, 'country_airports': 1}
NEXT
{'altitude': 13, 'longest': 11680, 'city': 'Brisbane', 'descr': 'Brisbane International Airport', 'iata': 'BNE', 'icao': 'YBBN', 'locat

In [215]:
r = graph.query("""Call gds.graph.drop("myGraph")""")
print(r)

[{'graphName': 'myGraph', 'database': 'neo4j', 'databaseLocation': 'local', 'memoryUsage': '', 'sizeInBytes': -1, 'nodeCount': 3503, 'relationshipCount': 46389, 'configuration': {'relationshipProjection': {'HAS_ROUTE': {'aggregation': 'DEFAULT', 'orientation': 'NATURAL', 'indexInverse': False, 'properties': {}, 'type': 'HAS_ROUTE'}}, 'readConcurrency': 4, 'relationshipProperties': {}, 'nodeProperties': {}, 'jobId': '72d360b1-8bd1-4647-91b2-51b1cbe6dbc9', 'nodeProjection': {'Airport': {'label': 'Airport', 'properties': {}}}, 'logProgress': True, 'creationTime': neo4j.time.DateTime(2024, 4, 15, 22, 14, 0, 938131131, tzinfo=<UTC>), 'validateRelationships': False, 'sudo': False}, 'density': 0.0037814532146957986, 'creationTime': neo4j.time.DateTime(2024, 4, 15, 22, 14, 0, 938131131, tzinfo=<UTC>), 'modificationTime': neo4j.time.DateTime(2024, 4, 15, 22, 14, 0, 971798975, tzinfo=<UTC>), 'schema': {'graphProperties': {}, 'nodes': {'Airport': {}}, 'relationships': {'HAS_ROUTE': {}}}, 'schemaW

# Random Walk


https://neo4j.com/docs/graph-data-science/current/algorithms/random-walk/

Random Walk is an algorithm that provides random paths in a graph.

A random walk simulates a traversal of the graph in which the traversed relationships are chosen at random. In a classic random walk, each relationship has the same, possibly weighted, probability of being picked. This probability is not influenced by the previously visited nodes. The random walk implementation of the Neo4j Graph Data Science library supports the concept of second order random walks. This method tries to model the transition probability based on the currently visited node v, the node t visited before the current one, and the node x which is the target of a candidate relationship. Random walks are thus influenced by two parameters: the returnFactor and the inOutFact

The returnFactor is used if t equals x, i.e., the random walk returns to the previously visited node.

The inOutFactor is used if the distance from t to x is equal to 2, i.e., the walk traverses further away from the node t


The probabilities for traversing a relationship during a random walk can be further influenced by specifying a relationshipWeightProperty. A relationship property value greater than 1 will increase the likelihood of a relationship being traversed, a property value between 0 and 1 will decrease that probability.
or

In [216]:
r = graph.query("""CALL gds.graph.project(
    'myGraph',
    'Airport',
    { HAS_ROUTE: { orientation: 'UNDIRECTED' } }
);""")
print(r)

[{'nodeProjection': {'Airport': {'label': 'Airport', 'properties': {}}}, 'relationshipProjection': {'HAS_ROUTE': {'aggregation': 'DEFAULT', 'orientation': 'UNDIRECTED', 'indexInverse': False, 'properties': {}, 'type': 'HAS_ROUTE'}}, 'graphName': 'myGraph', 'nodeCount': 3503, 'relationshipCount': 92778, 'projectMillis': 94}]


In [217]:
r = graph.query("""CALL gds.randomWalk.stream(
  'myGraph',
  {
    walkLength: 3,
    walksPerNode: 1,
    randomSeed: 42,
    concurrency: 1
  }
)
YIELD nodeIds, path
RETURN nodeIds, [node IN nodes(path) | node.descr ] AS pages""")


In [218]:
print(r[0])

{'nodeIds': [8627, 9047, 8632], 'pages': ['Hartsfield - Jackson Atlanta International Airport', 'Savannah Hilton Head International Airport', 'Baltimore/Washington International Airport']}


In [221]:
r = graph.query("""MATCH (airport:Airport)
WHERE airport.descr IN ['Marshall Islands International Airport', 'Boston Logan']
WITH COLLECT(airport) as sourceNodes
CALL gds.randomWalk.stream(
  'myGraph',
  {
    sourceNodes: sourceNodes,
    walkLength: 10,
    walksPerNode: 1,
    randomSeed: 42,
    concurrency: 1
  }
)
YIELD nodeIds, path
RETURN nodeIds, [node IN nodes(path) | node.descr ] AS Airports""")

In [222]:
r

[{'nodeIds': [8631, 8909, 8635, 8659, 8660, 8671, 8642, 8933, 8627, 8999],
  'Airports': ['Boston Logan',
   'Albany International Airport',
   'Fort Lauderdale/Hollywood International Airport',
   'San Antonio',
   'New Orleans L. Armstrong',
   'Philadelphia International Airport',
   'Miami International Airport',
   'Long Island Mac Arthur Airport',
   'Hartsfield - Jackson Atlanta International Airport',
   'Columbia Metropolitan Airport']},
 {'nodeIds': [9269, 9271, 9269, 8663, 8639, 8831, 9316, 9505, 8791, 8687],
  'Airports': ['Marshall Islands International Airport',
   'Bonriki International Airport',
   'Marshall Islands International Airport',
   'Honolulu International Airport',
   'Los Angeles International Airport',
   'Taiwan Taoyuan International Airport',
   'Naha Airport',
   'Taichung Ching Chuang Kang Airport',
   'Ho Chi Minh City, Tan Son Nhat International Airport',
   'Hong Kong - Chek Lap Kok International Airport']}]

In [223]:
r = graph.query("""Call gds.graph.drop("myGraph")""")
print(r)

[{'graphName': 'myGraph', 'database': 'neo4j', 'databaseLocation': 'local', 'memoryUsage': '', 'sizeInBytes': -1, 'nodeCount': 3503, 'relationshipCount': 92778, 'configuration': {'relationshipProjection': {'HAS_ROUTE': {'aggregation': 'DEFAULT', 'orientation': 'UNDIRECTED', 'indexInverse': False, 'properties': {}, 'type': 'HAS_ROUTE'}}, 'readConcurrency': 4, 'relationshipProperties': {}, 'nodeProperties': {}, 'jobId': '2bec7854-40a8-4453-a06a-9d02b9b1b079', 'nodeProjection': {'Airport': {'label': 'Airport', 'properties': {}}}, 'logProgress': True, 'creationTime': neo4j.time.DateTime(2024, 4, 15, 22, 18, 51, 875337052, tzinfo=<UTC>), 'validateRelationships': False, 'sudo': False}, 'density': 0.007562906429391597, 'creationTime': neo4j.time.DateTime(2024, 4, 15, 22, 18, 51, 875337052, tzinfo=<UTC>), 'modificationTime': neo4j.time.DateTime(2024, 4, 15, 22, 18, 51, 971238028, tzinfo=<UTC>), 'schema': {'graphProperties': {}, 'nodes': {'Airport': {}}, 'relationships': {'HAS_ROUTE': {}}}, 'sc

# Bellman-Ford Single-Source Shortest Path
https://neo4j.com/docs/graph-data-science/current/algorithms/bellman-ford-single-source/
/
The Bellman-Ford Path algorithm computes the shortest path between nodes.

In contrast to the Dijkstra algorithm which works only for graphs with non-negative relationship weights, Bellman-Ford can also handle graphs with negative weights provided that the source cannot reach any node involved in a negative cycle. A cycle in a graph is a path starting and ending at the same node. A negative cycle is a cycle for which the sum of the relationship weights is negative. When negative cycles exist, shortest paths cannot easily be defined. That is so because we can traverse a negative cycle multiple times to get smaller and smaller costs each time.

When the Bellman-Ford algorithm detects negative cycles, it will return negative cycles instead of shortest paths. As the full set of negative cycles can be too large to enumerate, each node will be included in at most one returned negative cycle.

The ability to handle negative weights makes Bellman-Ford more versatile than Dijkstra, but also slower in practice..

In [93]:
r = graph.query("""CREATE (a:Node {name: 'A'}),
       (b:Node {name: 'B'}),
       (c:Node {name: 'C'}),
       (d:Node {name: 'D'}),
       (e:Node {name: 'E'}),
       (f:Node {name: 'F'}),
       (g:Node {name: 'G'}),
       (h:Node {name: 'H'}),
       (i:Node {name: 'I'}),
       (a)-[:REL {cost: 50}]->(b),
       (a)-[:REL {cost: -50}]->(c),
       (a)-[:REL {cost: 100}]->(d),
       (b)-[:REL {cost: 40}]->(d),
       (c)-[:REL {cost: 40}]->(d),
       (c)-[:REL {cost: 80}]->(e),
       (d)-[:REL {cost: 30}]->(e),
       (d)-[:REL {cost: 80}]->(f),
       (e)-[:REL {cost: 40}]->(f),
       (g)-[:REL {cost: 40}]->(h),
       (h)-[:REL {cost: -60}]->(i),
       (i)-[:REL {cost: 10}]->(g)""")


In [224]:
r = graph.query("""CALL gds.graph.project(
    'myGraph',
    'Node',
    'REL',
    {
        relationshipProperties: 'cost'
    }
)""")
print(r)

[{'nodeProjection': {'Node': {'label': 'Node', 'properties': {}}}, 'relationshipProjection': {'REL': {'aggregation': 'DEFAULT', 'orientation': 'NATURAL', 'indexInverse': False, 'properties': {'cost': {'aggregation': 'DEFAULT', 'property': 'cost', 'defaultValue': None}}, 'type': 'REL'}}, 'graphName': 'myGraph', 'nodeCount': 9, 'relationshipCount': 12, 'projectMillis': 13}]


In [156]:
r = graph.query("""MATCH (source:Node {name: 'A'})
CALL gds.bellmanFord.write.estimate('myGraph', {
    sourceNode: source,
    relationshipWeightProperty: 'cost',
    writeRelationshipType: 'PATH'
})
YIELD nodeCount, relationshipCount, bytesMin, bytesMax, requiredMemory
RETURN nodeCount, relationshipCount, bytesMin, bytesMax, requiredMemory""")
print(r)

[{'nodeCount': 9, 'relationshipCount': 12, 'bytesMin': 1712, 'bytesMax': 1712, 'requiredMemory': '1712 Bytes'}]


In [225]:
r = graph.query("""MATCH (source:Node {name: 'A'})
CALL gds.bellmanFord.stream('myGraph', {
    sourceNode: source,
    relationshipWeightProperty: 'cost'
})
YIELD index, sourceNode, targetNode, totalCost, nodeIds, costs, route, isNegativeCycle
RETURN
    index,
    gds.util.asNode(sourceNode).name AS sourceNode,
    gds.util.asNode(targetNode).name AS targetNode,
    totalCost,
    [nodeId IN nodeIds | gds.util.asNode(nodeId).name] AS nodeNames,
    costs,
    nodes(route) as route,
    isNegativeCycle as isNegativeCycle
ORDER BY index""")


In [226]:
for s in r:
    print(s)

{'index': 0, 'sourceNode': 'A', 'targetNode': 'A', 'totalCost': 0.0, 'nodeNames': ['A'], 'costs': [0.0], 'route': [{'name': 'A'}], 'isNegativeCycle': False}
{'index': 1, 'sourceNode': 'A', 'targetNode': 'B', 'totalCost': 50.0, 'nodeNames': ['A', 'B'], 'costs': [0.0, 50.0], 'route': [{'name': 'A'}, {'name': 'B'}], 'isNegativeCycle': False}
{'index': 2, 'sourceNode': 'A', 'targetNode': 'C', 'totalCost': -50.0, 'nodeNames': ['A', 'C'], 'costs': [0.0, -50.0], 'route': [{'name': 'A'}, {'name': 'C'}], 'isNegativeCycle': False}
{'index': 3, 'sourceNode': 'A', 'targetNode': 'D', 'totalCost': -10.0, 'nodeNames': ['A', 'C', 'D'], 'costs': [0.0, -50.0, -10.0], 'route': [{'name': 'A'}, {'name': 'C'}, {'name': 'D'}], 'isNegativeCycle': False}
{'index': 4, 'sourceNode': 'A', 'targetNode': 'E', 'totalCost': 20.0, 'nodeNames': ['A', 'C', 'D', 'E'], 'costs': [0.0, -50.0, -10.0, 20.0], 'route': [{'name': 'A'}, {'name': 'C'}, {'name': 'D'}, {'name': 'E'}], 'isNegativeCycle': False}
{'index': 5, 'sourceNo

In [159]:
# Stream with negative cycles
r = graph.query("""MATCH (source:Node {name: 'G'})
CALL gds.bellmanFord.stream('myGraph', {
    sourceNode: source,
    relationshipWeightProperty: 'cost'
})
YIELD index, sourceNode, targetNode, totalCost, nodeIds, costs, route, isNegativeCycle
RETURN
    index,
    gds.util.asNode(sourceNode).name AS sourceNode,
    gds.util.asNode(targetNode).name AS targetNode,
    totalCost,
    [nodeId IN nodeIds | gds.util.asNode(nodeId).name] AS nodeNames,
    costs,
    nodes(route) as route,
    isNegativeCycle as isNegativeCycle
ORDER BY index""")
print(r)

[{'index': 0, 'sourceNode': 'G', 'targetNode': 'G', 'totalCost': -10.0, 'nodeNames': ['G', 'H', 'I', 'G'], 'costs': [0.0, 40.0, -20.0, -10.0], 'route': [{'name': 'G'}, {'name': 'H'}, {'name': 'I'}, {'name': 'G'}], 'isNegativeCycle': True}]


In [160]:
for s in r:
    print(s)

{'index': 0, 'sourceNode': 'G', 'targetNode': 'G', 'totalCost': -10.0, 'nodeNames': ['G', 'H', 'I', 'G'], 'costs': [0.0, 40.0, -20.0, -10.0], 'route': [{'name': 'G'}, {'name': 'H'}, {'name': 'I'}, {'name': 'G'}], 'isNegativeCycle': True}


In [101]:
r = graph.query("""Call gds.graph.drop("myGraph")""")
print(r)

[{'graphName': 'myGraph', 'database': 'neo4j', 'databaseLocation': 'local', 'memoryUsage': '', 'sizeInBytes': -1, 'nodeCount': 9, 'relationshipCount': 12, 'configuration': {'relationshipProjection': {'REL': {'aggregation': 'DEFAULT', 'orientation': 'NATURAL', 'indexInverse': False, 'properties': {'cost': {'aggregation': 'DEFAULT', 'property': 'cost', 'defaultValue': None}}, 'type': 'REL'}}, 'readConcurrency': 4, 'relationshipProperties': {}, 'nodeProperties': {}, 'jobId': 'ec3ea204-0b0a-4f0b-93fe-0f261c4dc13a', 'nodeProjection': {'Node': {'label': 'Node', 'properties': {}}}, 'logProgress': True, 'creationTime': neo4j.time.DateTime(2024, 4, 15, 18, 46, 47, 955929328, tzinfo=<UTC>), 'validateRelationships': False, 'sudo': False}, 'density': 0.16666666666666666, 'creationTime': neo4j.time.DateTime(2024, 4, 15, 18, 46, 47, 955929328, tzinfo=<UTC>), 'modificationTime': neo4j.time.DateTime(2024, 4, 15, 18, 46, 47, 987539725, tzinfo=<UTC>), 'schema': {'graphProperties': {}, 'nodes': {'Node': 

# Minimum Weight Spanning Tree

https://neo4j.com/docs/graph-data-science/current/algorithms/minimum-weight-spanning-tree/


The Minimum Weight Spanning Tree (MST) starts from a given node, finds all its reachable nodes and returns the set of relationships that connect these nodes together having the minimum possible weight. Prim’s algorithm is one of the simplest and best-known minimum spanning tree algorithms. It operates similarly to Dijkstra’s shortest path algorithm, but instead of minimizing the total length of a path ending at each relationship, it minimizes the length of each relationship individually. This allows the algorithm to work on graphs with negative weights.

In [102]:
r = graph.query("""CALL gds.graph.project(
    'myGraph',
    'Airport',
    { HAS_ROUTE: { properties: 'distance', orientation: 'UNDIRECTED' } }
);""")
print(r)

[{'nodeProjection': {'Airport': {'label': 'Airport', 'properties': {}}}, 'relationshipProjection': {'HAS_ROUTE': {'aggregation': 'DEFAULT', 'orientation': 'UNDIRECTED', 'indexInverse': False, 'properties': {'distance': {'aggregation': 'DEFAULT', 'property': 'distance', 'defaultValue': None}}, 'type': 'HAS_ROUTE'}}, 'graphName': 'myGraph', 'nodeCount': 3503, 'relationshipCount': 92778, 'projectMillis': 292}]


In [104]:
r = graph.query("""MATCH (n:Airport {descr: 'Boston Logan'})
CALL gds.spanningTree.stats.estimate('myGraph', {sourceNode: id(n),relationshipWeightProperty:'distance'})
YIELD nodeCount, relationshipCount, bytesMin, bytesMax, requiredMemory
RETURN nodeCount, relationshipCount, bytesMin, bytesMax, requiredMemory""")
print(r)

[{'nodeCount': 3503, 'relationshipCount': 92778, 'bytesMin': 112944, 'bytesMax': 112944, 'requiredMemory': '110 KiB'}]


In [106]:
r = graph.query("""MATCH (n:Airport {descr: 'Boston Logan'})
CALL gds.spanningTree.stream('myGraph', {
  sourceNode: n,
  relationshipWeightProperty: 'distance'
})
YIELD nodeId,parentId, weight
RETURN gds.util.asNode(nodeId).descr AS node, gds.util.asNode(parentId).descr AS parent,weight
ORDER BY node""")


In [111]:
for d in r[:20]:
    print(d)


{'node': 'A Coruna Airport', 'parent': 'Bilbao Airport', 'weight': 275.0}
{'node': 'Aalborg Airport', 'parent': 'Aarhus Airport', 'weight': 62.0}
{'node': 'Aarhus Airport', 'parent': 'Copenhagen Kastrup Airport', 'weight': 92.0}
{'node': 'Aasiaat Airport', 'parent': 'Kangerlussuaq Airport', 'weight': 130.0}
{'node': 'Aba Tenna Dejazmach Yilma International Airport', 'parent': 'Djibouti-Ambouli Airport', 'weight': 160.0}
{'node': 'Abadan Airport', 'parent': 'Shiraz Shahid Dastghaib International Airport', 'weight': 267.0}
{'node': 'Abakan Airport', 'parent': 'Irkutsk Airport', 'weight': 549.0}
{'node': 'Abbotsford Airport', 'parent': 'Calgary International Airport', 'weight': 397.0}
{'node': 'Abdul Rachman Saleh Airport', 'parent': 'Bali - Ngurah Rai International Airport', 'weight': 177.0}
{'node': 'Abeche Airport', 'parent': "N'Djamena International Airport", 'weight': 408.0}
{'node': 'Abeid Amani Karume International Airport', 'parent': 'Mombasa Moi International Airport', 'weight': 

In [112]:
r[0]

{'node': 'A Coruna Airport', 'parent': 'Bilbao Airport', 'weight': 275.0}